In [46]:
import pandas as pd
import numpy as np
from datetime import timedelta
from dateutil.relativedelta import relativedelta
import statsmodels as sm
import statsmodels.api as sm
import statsmodels.formula.api as smf
import statistics
import pytse_client as tse
from scipy.stats import ttest_1samp
from statsmodels.api import add_constant
import math
from scipy.stats import norm

In [3]:
Data = tse.download(symbols="all", write_to_csv=True)

In [4]:
Data

{'غویتا':                open     high      low  adjClose         value    volume  \
 date                                                                      
 2019-07-08  12300.0  12300.0  12300.0   12300.0  155093529000  12609230   
 2019-07-09  12915.0  12915.0  12915.0   12915.0   48132590625   3726875   
 2019-07-10  13560.0  13560.0  13560.0   13560.0   66789902040   4925509   
 2019-07-13  14238.0  14238.0  13610.0   14135.0  168742491025  11938240   
 2019-07-14  14470.0  14470.0  13702.0   13988.0   45325735300   3240337   
 2019-07-15  14237.0  14599.0  14014.0   14261.0   42634559750   2989650   
 2019-07-16  14000.0  14300.0  13548.0   13581.0   26225790693   1931076   
 2019-07-17  13000.0  14260.0  12910.0   13974.0   78517893685   5619018   
 2019-07-20  14010.0  14444.0  13700.0   13977.0   21629431661   1547536   
 2019-07-21  14048.0  14048.0  13279.0   13433.0   26806675074   1995627   
 2019-07-22  13291.0  13700.0  13291.0   13455.0   16282150758   1210140   
 20

In [6]:
# Data Cleaning and Initialization
StockData=[]
for i in Data:
    StockData.append(i)
    
Data_list=[]
for j in StockData:
    Data_list.append(Data[j].iloc[:,3])
Stock=pd.concat(Data_list,axis=1, join='outer')

Stock.columns= [str(x) for x in StockData]

In [7]:
Stock.to_excel("output.xlsx",sheet_name='Sheet_name_1')

In [7]:
# Data Cleaning and Initialization, Daily Return Data set
price1=Stock.iloc[0:(len(Stock)-1)].values
price2=Stock.iloc[1:(len(Stock))]
DailyReturn=(price2-price1)/price1
#DailyReturn=DailyReturn.fillna(method='ffill').fillna(method='bfill')
# Adding a column as market return
Market_Return=[]
for i in range(len(DailyReturn)):
    Market_Return.append(DailyReturn.iloc[i].mean())
DailyReturn['RM']=Market_Return
#DailyReturn      # Our main Dataset

In [8]:
RMarket=DailyReturn['RM']
RMarket=pd.DataFrame(RMarket)

In [10]:
# Monthly Return
Final=DailyReturn.sub(RMarket,fill_value=0)
Final
ReturnM=Final.resample('M', convention='start').sum()
#ReturnM=ReturnM.replace(0.000,"Nan")
ReturnM=ReturnM.drop(['RM'],axis=1)

In [ ]:
# CAR and ACAR
FormationPeriod=[1,2,3,6,12,36,60]
TestPeriod=[1,2,3,6,12,24,36,48,60]
Winners,Losers,CARWinner,CARLoser,CARBuy_Hold,ACARWinner,ACARLoser,ACAR_Buy_Hold,ACARWin,ACARLose,ACARBH,PvalWin,PvalLose,PvalBH=[],[],[],[],[],[],[],[],[],[],[],[],[],[]
for i in FormationPeriod:   
    ACARWinner,ACARLoser,ACAR_Buy_Hold=[],[],[]
    Pval_Winner,Pval_Loser,Pval_Buy_Hold=[],[],[]
    for j in TestPeriod:
        FormationDate=i
        CARWinner,CARLoser,CARBuy_Hold=[],[],[]
        while (FormationDate+j)<len(ReturnM):
            Winners=(ReturnM.iloc[(FormationDate-i):FormationDate].sum()).nlargest(5)
            Losers=(ReturnM.iloc[(FormationDate-i):FormationDate].sum()).nsmallest(5)
            sub_Data=ReturnM.iloc[FormationDate:(FormationDate+j)]
            sub_Data.replace(0,np.nan, inplace=True)
            WinnerPortfo = (pd.DataFrame(np.column_stack([sub_Data[Winners.index[0]],sub_Data[Winners.index[1]],sub_Data[Winners.index[2]],sub_Data[Winners.index[3]],sub_Data[Winners.index[4]]]))).apply(lambda x: x.fillna(x.mean()),axis=1)
            LoserPortfo = (pd.DataFrame(np.column_stack([sub_Data[Losers.index[0]],sub_Data[Losers.index[1]],sub_Data[Losers.index[2]],sub_Data[Losers.index[3]],sub_Data[Losers.index[4]]]))).apply(lambda x: x.fillna(x.mean()),axis=1)
            CARWinner.append((WinnerPortfo.sum()/5).sum())
            CARLoser.append((LoserPortfo.sum()/5).sum())
            CARBuy_Hold.append((LoserPortfo.sum()/5).sum()-(WinnerPortfo.sum()/5).sum())
            FormationDate=FormationDate+i
        ACARWinner.append(statistics.mean(CARWinner))
        ACARLoser.append(statistics.mean(CARLoser))
        ACAR_Buy_Hold.append(statistics.mean(CARBuy_Hold))
        Pval_Winner.append(ttest_1samp(CARWinner, 0)[1])
        Pval_Loser.append(ttest_1samp(CARLoser, 0)[1])
        Pval_Buy_Hold.append(ttest_1samp(CARBuy_Hold, 0)[1])
    ACARWin.append(ACARWinner)
    ACARLose.append(ACARLoser)
    ACARBH.append(ACAR_Buy_Hold)
    PvalWin.append(Pval_Winner)
    PvalLose.append(Pval_Loser)
    PvalBH.append(Pval_Buy_Hold)
ACARWin=pd.DataFrame(ACARWin)
ACARLose=pd.DataFrame(ACARLose)
ACARBH=pd.DataFrame(ACARBH)
PvalWin=pd.DataFrame(PvalWin)
PvalLose=pd.DataFrame(PvalLose)
PvalBH=pd.DataFrame(PvalBH)

In [13]:
Results=pd.DataFrame()
for i in range(7):
    Results=Results.append(ACARWin.iloc[i]).append(PvalWin.iloc[i]).append(ACARLose.iloc[i]).append(PvalLose.iloc[i]).append(ACARBH.iloc[i]).append(PvalBH.iloc[i])
Results.to_excel("Results.xlsx",sheet_name='Sheet1')

In [15]:
Riskfree = pd.read_excel (r'C:\Users\Asus\Desktop\riskfree.xlsx')
Riskfree
RMarketMonthly=RMarket.resample('M', convention='start').sum()
RMarketMonthly
Rf=[]
for i in range(len(Riskfree)):
    for j in range(12):
        Rf.append(Riskfree.iloc[i][2])       
Rf=Rf[2:(len(Rf)-4)]
BasicReturn=ReturnM
BasicReturn['rf']=Rf
BasicReturn['RM']=RMarketMonthly['RM']
BasicReturn['Rm-Rf']=BasicReturn['RM'].subtract(BasicReturn['rf'])

In [16]:
def dot_Product(X,Y):
    Product=np.empty(len(X))
    for i in range(len(X)):
        Product[i]=X[i]*Y[i]
    return Product


In [135]:
FormationPeriod=3
TestPeriod=1
Winners,Losers=[],[]
alpha_F,alpha_T,beta_F,beta_T=[],[],[],[]
Tstat_alpha_F,Tstat_alpha_T,Tstat_beta_F,Tstat_beta_T=[],[],[],[]
Size=[]
i=FormationPeriod 
j=TestPeriod
FormationDate=i
Rf,Rm,RmRf=[],[],[]
Results_Buy_Hold=[]
while (FormationDate+j)<len(ReturnM):
    Winners=(ReturnM.iloc[(FormationDate-i):FormationDate].sum()).nlargest(5)
    Losers=(ReturnM.iloc[(FormationDate-i):FormationDate].sum()).nsmallest(5)
    sub_Data=ReturnM.iloc[(FormationDate-i):(FormationDate+j)]
    #sub_Data.replace(0,np.nan, inplace=True)
    WinnerPortfo = (pd.DataFrame(np.column_stack([sub_Data[Winners.index[0]],sub_Data[Winners.index[1]],sub_Data[Winners.index[2]],sub_Data[Winners.index[3]],sub_Data[Winners.index[4]]]))).apply(lambda x: x.fillna(x.mean()),axis=1)
    LoserPortfo = (pd.DataFrame(np.column_stack([sub_Data[Losers.index[0]],sub_Data[Losers.index[1]],sub_Data[Losers.index[2]],sub_Data[Losers.index[3]],sub_Data[Losers.index[4]]]))).apply(lambda x: x.fillna(x.mean()),axis=1)
    pd.DataFrame(WinnerPortfo.mean(axis=1))
    pd.DataFrame(LoserPortfo.mean(axis=1))
    Rf=BasicReturn['rf'].iloc[(FormationDate-i):(FormationDate+j)]
    Rm=BasicReturn['RM'].iloc[(FormationDate-i):(FormationDate+j)]
    RmRf=BasicReturn['Rm-Rf'].iloc[(FormationDate-i):(FormationDate+j)]
    Intercept=np.ones(len(Rf))
    Dummy = np.ones(len(Rf))
    t=0
    while t<i:
        Dummy[t]=0
        t=t+1
    Matrix_Winner=pd.DataFrame(np.column_stack([WinnerPortfo.mean(axis=1),Intercept,Dummy,RmRf,dot_Product(np.array(RmRf),Dummy)]))
    Matrix_Loser=pd.DataFrame(np.column_stack([LoserPortfo.mean(axis=1),Intercept,Dummy,RmRf,dot_Product(np.array(RmRf),Dummy)]))
    Matrix_Buy_Hold=pd.DataFrame(np.column_stack([(LoserPortfo.mean(axis=1)-WinnerPortfo.mean(axis=1)),Intercept,Dummy,RmRf,dot_Product(np.array(RmRf),Dummy)]))
    res = sm.OLS(Matrix_Buy_Hold[0], Matrix_Buy_Hold[[1,2,3,4]]).fit()
    alpha_F.append(res.params.iloc[0])
    alpha_T.append(res.params.iloc[1])
    beta_F.append(res.params.iloc[2])
    beta_T.append(res.params.iloc[3])
    Tstat_alpha_F.append(res.tvalues.iloc[0])
    Tstat_alpha_T.append(res.tvalues.iloc[1])
    Tstat_beta_F.append(res.tvalues.iloc[2])
    Tstat_beta_T.append(res.tvalues.iloc[3])
    Size.append(len(Rf))
    FormationDate=FormationDate+i
        

In [65]:
def U_Statistic(alpha,Tstat,Size):
    Sum_alpha=0
    Sum_U=0
    for i in range(len(Size)):
        Sum_alpha+=alpha[i]*Size[i]
        Sum_U+=Tstat[i]*(((Size[i]-3)/(Size[i]-1))**(0.5))
    alpha_average=Sum_alpha/(sum(Size))
    U=(len(Size)**(-0.5))*Sum_U
    if U>0:
        pvalue_U=2*abs(1-norm.cdf(U))
    else:
        pvalue_U=2*abs(norm.cdf(U))
    return alpha_average,U,pvalue_U

In [136]:
U_Statistic(alpha_F,Tstat_alpha_F,Size)

(-0.39575252309630576, -49.49428802231973, 0.0)

In [140]:
U_Statistic(alpha_T,Tstat_alpha_T,Size)

(0.38941892868902, 24.571190028330825, 0.0)

In [141]:
U_Statistic(beta_F,Tstat_beta_F,Size)

(-0.27625540864694126, -4.28186196845097, 1.8533593996159128e-05)

In [142]:
U_Statistic(beta_T,Tstat_beta_T,Size)

(0.4039812542325294, 2.7523359690399514, 0.005917178114498434)

In [143]:
len(Size)

81

In [374]:
Matrix_Buy_Hold
Matrix_Buy_Hold.to_excel("output.xlsx",sheet_name='Sheet_name_3')

In [332]:
Results_Buy_Hold=pd.DataFrame(Results_Buy_Hold)
Results_Buy_Hold

0             1             2         3
0   1.445522e-01 -3.343647e-02  9.583633e-01 -0.071749
1   2.700726e-06  2.442320e-01  1.826796e-02  0.861806
2   2.148752e-01 -1.446515e-01  1.234483e+00 -1.021071
3   4.698778e-05  4.634147e-03  2.418678e-02  0.066423
4   1.771035e-01 -9.044139e-02  8.079078e-01 -0.224929
5   1.945391e-03  1.047938e-01  3.367040e-01  0.789873
6   2.501245e-01 -1.330419e-01  1.681517e+00 -0.969051
7   5.660206e-06  9.492363e-03  1.990005e-03  0.067991
8   2.707237e-01 -2.261356e-01  1.140751e+00 -0.663365
9   2.613907e-11  4.800369e-07  3.184506e-03  0.118789
10  2.550804e-01 -1.627980e-01  1.141556e+00 -0.678661
11  1.970253e-06  1.808153e-03  3.456883e-02  0.216292
12  3.736546e-01 -2.984682e-01  2.359685e+00 -1.570942
13  4.751900e-11  5.650480e-07  3.016657e-04  0.017728
14  3.063740e-01 -1.545156e-01  1.581643e+00 -0.517189
15  5.950186e-14  1.160426e-04  7.405337e-09  0.082172
16  5.037021e-01 -3.586011e-01  3.083965e+00 -2.170558
17  2.137892e-12  7.052502e-08  6.103412e-10  0.000006
18  2.224377e-01 -1.020465e-01  9.414856e-01 -0.274051
19  3.320379e-03  2.278298e-01  5.361567e-02  0.646873
20  3.157230e-01 -1.377584e-01  1.947964e+00 -0.693264
21  1.845976e-02  3.002095e-01  1.237573e-01  0.585196
22  7.141034e-02  5.107574e-02 -6.488317e-01  1.423240
23  4.973891e-01  6.377274e-01  4.690856e-01  0.129072
24  3.378602e-01 -2.334025e-01  1.980497e+00 -1.242402
25  6.868531e-02  2.046770e-01  2.034442e-01  0.423638
26  2.716433e-01 -1.517180e-01  1.417826e+00 -0.821627
27  2.619645e-06  4.787965e-03  1.655658e-03  0.065504
28  3.180075e-01 -2.226974e-01  2.029197e+00 -1.442452
29  1.064010e-04  4.924737e-03  4.153913e-03  0.039341
..           ...           ...           ...       ...
38  3.930800e-01 -3.127983e-01  1.543963e+00 -1.220016
39  2.457767e-08  4.418156e-06  3.942623e-03  0.024706
40  3.449778e-01 -2.679837e-01  1.386972e+00 -0.660285
41  3.575034e-05  1.162110e-03  5.375125e-02  0.360982
42  6.108994e-02  1.944503e-02 -1.284374e+00  2.088270
43  5.152575e-01  8.416526e-01  1.066176e-01  0.013152
44  2.921559e-01 -1.864160e-01  1.079126e+00 -0.397454
45  2.688827e-03  5.231475e-02  8.537111e-02  0.531189
46  1.541249e-01 -2.972723e-02 -5.465208e-01  1.537196
47  4.710277e-03  5.902130e-01  2.845816e-01  0.005581
48  2.592873e-01 -1.648010e-01  5.047754e-01  0.269124
49  1.344513e-10  6.877668e-05  2.524008e-01  0.563116
50  3.100975e-01 -1.587684e-01  1.511369e+00 -0.376334
51  2.280634e-08  9.339885e-03  2.116454e-05  0.370308
52  1.451215e-01 -8.273947e-02 -1.877295e-01  0.289679
53  1.809930e-02  1.986775e-01  6.250176e-01  0.497051
54  5.603476e-01 -4.321294e-01  2.154834e+00 -1.153320
55  2.803883e-04  7.586415e-03  2.827484e-02  0.286347
56  1.547748e-01 -7.338349e-02  1.154243e-01  0.299772
57  3.376963e-01  6.565182e-01  9.147668e-01  0.789730
58  1.863826e-01 -6.431053e-02  7.550319e-02  0.784890
59  1.347788e-04  1.754710e-01  8.337079e-01  0.042074
60  8.133478e-02  2.737833e-03 -8.312699e-01  1.580740
61  8.043674e-01  9.933544e-01  7.584199e-01  0.559740
62  2.664636e-01 -1.488199e-01  9.046225e-01 -0.244262
63  4.648530e-03  1.034295e-01  2.197501e-01  0.739388
64  5.441152e-01 -4.302217e-01  2.778553e+00 -1.904045
65  5.604383e-04  5.632695e-03  6.109885e-02  0.197044
66  7.485725e-01 -6.442889e-01  4.081501e+00 -3.475894
67  3.769733e-04  1.852133e-03  6.792400e-03  0.019878

[68 rows x 4 columns]